In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install PyPDF2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 kB 4.6 MB/s eta 0:00:00


In [ ]:
import firebase_admin
from firebase_admin import credentials, firestore

cred = credentials.Certificate('/content/drive/MyDrive/itpe_exams/exam-matching-firebase-adminsdk-hdm65-231e235b83.json')
firebase_admin.initialize_app(cred)

db = firestore.client()

# **Question Library**

In [ ]:
import os
import re
import PyPDF2
import pandas as pd

fe_path = '/content/drive/MyDrive/itpe_exams/FE/questions'
ip_path = '/content/drive/MyDrive/itpe_exams/IP/questions'
fe_question_image_path = ''
ip_question_image_path = ''
fe_answer_image_path = ''
ip_answer_image_path = ''

def clean_question(question):
  question = re.sub(r'^q\d+\.\s', '', question)
  # question = question.replace('\n', '')
  question = re.sub(r'\s+', ' ', question)
  return question.strip()

def find_questions_and_answers(text, file_name):
  questions_answer = re.findall(
      r'(Q\d+\..*?)\s*a\)(.*?)\s*b\)(.*?)\s*c\)(.*?)\s*d\)(.*?)\n',
      text,
      re.DOTALL)
  result = []

  for qa in questions_answer:
    question_number = qa[0][0:3]
    question = clean_question(qa[0])
    answers = [answer.strip() for answer in qa[1:]]# รวมคำตอบทั้งหมดที่ไม่ใช่ None

    # question = question.replace('\n', '')
    # embedding_vector = model.encode(question, convert_to_tensor=True)
    question_number = question_number.replace('.','')
    result.append({
            'filename': file_name,
            'question_number': int(question_number[1:]),
            'question': question,
            'answers': answers,
            # 'embedding_vector': embedding_vector
        })
  return result

def get_data(path):
  all_questions = []
  for filename in os.listdir(path):
    if filename.endswith('.pdf'):
      file_path = os.path.join(path, filename)

      with open(file_path, 'rb') as file:
        pdf_reader = PyPDF2.PdfReader(file)
        text = ''
        for page in pdf_reader.pages:
          text += page.extract_text()
          questions = find_questions_and_answers(text,filename)
          all_questions.extend(questions)

  return all_questions

fe = get_data(fe_path)
ip = get_data(ip_path)

In [ ]:
fe[0]

{'filename': '2009Apr_FE_AM_Questions.pdf',
 'question_number': 1,
 'question': 'Q1. In which month is the spring Fundamental IT Engineer Examination conducted?',
 'answers': ['March', 'April', 'May', 'June']}

In [ ]:
fe_answer_path = '/content/drive/MyDrive/itpe_exams/FE/answers'
ip_answer_path = '/content/drive/MyDrive/itpe_exams/IP/answers'

def find_answers_fe(text, file_name):
  matches = re.findall(
      r'(Q\d+)\s+([a-d])',
      text,
      re.DOTALL)
  result = []

  for match in matches:
    question_number, answer = match
    result.append({
            'filename': file_name,
            'question_number': int(question_number[1:]),
            'answers': answer
        })
  return result

def find_answers_ip(text, file_name):
  matches = re.findall(
      r'(\d+)\s+([a-d])',
      text,
      re.DOTALL)
  result = []

  for match in matches:
    question_number, answer = match
    result.append({
            'filename': file_name,
            'question_number': int(question_number),
            'answers': answer
        })
  return result

def get_data(path, is_fe):
  all_answers = []
  for filename in os.listdir(path):
    if filename.endswith('.pdf'):
      file_path = os.path.join(path, filename)

      with open(file_path, 'rb') as file:
        pdf_reader = PyPDF2.PdfReader(file)
        text = ''
        for page in pdf_reader.pages:
          text += page.extract_text()
          if is_fe:
            answers = find_answers_fe(text,filename)
          else:
            answers = find_answers_ip(text,filename)
          all_answers.extend(answers)


  return all_answers

fe_answers = get_data(fe_answer_path, True)
ip_answers = get_data(ip_answer_path, False)

In [ ]:
fe_answers[0]

{'filename': '2009Apr_FE_AM_Answers.pdf', 'question_number': 1, 'answers': 'b'}

In [ ]:
from sentence_transformers import SentenceTransformer

fe_copy = fe.copy()
ip_copy = ip.copy()

model = SentenceTransformer('all-MiniLM-L6-V2')
unique_questions = set()
result = []

combined_list = fe_copy + ip_copy

for item in combined_list:
  question = item.get("question")  # ดึงค่า key 'question'

  if question.startswith("Q1. In which month"):
    continue
  if question not in unique_questions:
    unique_questions.add(question)
    result.append(item)

exams = []
for item in result:
  item['question'] = item['question'].replace('\n', '')
  embedding_vector = model.encode(item['question'], convert_to_tensor=True)
  item['embedding_vector'] = embedding_vector
  exams.append(item)

In [ ]:
for question in exams:
  for answer in fe_answers:
    if (question['question_number'] == answer['question_number']) and (question['filename'][:-14].lower() == answer['filename'][:-12].lower()):
      question['correct_answer'] = answer['answers']

for question in exams:
  for answer in ip_answers:
    if (question['question_number'] == answer['question_number']) and (question['filename'][:-14].lower() == answer['filename'][:-12].lower()):
      question['correct_answer'] = answer['answers']

In [ ]:
exams[400]

{'filename': '2011S_FE_PM_Questions.pdf',
 'question_number': 2,
 'question': 'Q2. Read the following description concerning vi rtual memory controls, and then answer Subquestion. There is a computer with a ddress space of 8k bytes (virtual addresses: 0 to 8191) and a physical memory (main memory) of 4k bytes ( physical addresses: 0 to 4095). Its virtual memory has virtual page size of 1024 bytes, 8 virtual pages, and its physical memory has page frame size of 1024 bytes, 4 page frames. Figure 1(',
 'answers': ['illustrates the way to divide up \nthe address space of 8k bytes into  8 virtual pages, and Figure 1(',
  'illustrates the way to \ndivide up the physical memory of 4k bytes into 4 page frames. \n \n Virtual \naddress    \n 0 \uf0e0 Virtual page 0 } 1k\n 1024 \uf0e0 Virtual page 1  \n 2048 \uf0e0 Virtual page 2  \n 3072 \uf0e0 Virtual page 3  \n 4096 \uf0e0 Virtual page 4  \n 5120 \uf0e0 Virtual page 5  \n 6144 \uf0e0 Virtual page 6  \n 7168 \uf0e0 Virtual page 7  \n     \na) A

In [ ]:
def add_data_to_firestore(data):
    try:
      db.collection('exams').add({
        'exam_name': item['filename'],
        'question_number': item['question_number'],
        'question': item['question'],
        'answers': item['answers'],
        # 'correct_answer': item['correct_answer']
    })
    except Exception as e:
      print(e)
      print(item)

for item in result:
  add_data_to_firestore(item)

# **Clustering**

## **Text Prep**

In [ ]:
qid = db.collection('exams').stream()
id = [id.id for id in qid]
qid = [id.to_dict() for id in qid]

In [ ]:
id

['00BIC4wIflXSsvOO7MBa',
 '00Q6RDxYvNgcPCwg2tXg',
 '00bkasubJySUQFp0zvlu',
 '012H0gVUcCApoodLY5gD',
 '016FY0dqdVBGLbZ4dNG5',
 '028dfSQmdKHOFxMyJGGX',
 '02ToTKBNQR6iIrwPCFiV',
 '03ThLj1QfEt9l4HGNQ1B',
 '046BXLm4lluKv3vPgz9A',
 '05pwpo5ofSNic1DYjIa1',
 '05uM9FHIIybegqF2sNrT',
 '06zqS3mUGD21TLU9qRvx',
 '074I8RabTj8v6hjcFHBw',
 '07glMEYOnxC3bUuDqS1g',
 '07kX3ENOucrVrhHeY4Q7',
 '08aQ3WVXh8aMn7fyLJNN',
 '08dFrcglxiTyDFKgzDdi',
 '08gvaWV97fIUZfzFlDoR',
 '08hECPxU9K04w3CTGdvC',
 '09Tmyn2ze2IIwmnmxMSi',
 '0ABOOIXUhGRMuHmFWgmL',
 '0BoqmsV02GhFR2Fx3RmM',
 '0CJ7XmvNWvQd69aR5CtE',
 '0Cl1rEwRoY4ziILsIzw3',
 '0D96386tOsngz4VjuoYP',
 '0F4Kh7WsnZRJCwY0HSgc',
 '0FdOXmyth5UnVuMLo8rt',
 '0H8OJYvWSuNlTojg4Yji',
 '0ITC5GBJywc5Er0dLl7J',
 '0JcVkpmbYAk0itrea3Ss',
 '0Jldhqftc80toDLHzicZ',
 '0L7VgF2UzQS3mL8AqytD',
 '0LHYd30YyeQhk1jRE0uU',
 '0LyKbAzfjnkwMe689uEi',
 '0ML0coGadUpWdt0C4lLd',
 '0MXxpMhPirfaBLROTd08',
 '0MlV6V2FvOYOV0PVLyqL',
 '0NOE9cTPjxDejPgul8RZ',
 '0NOT8ZknRUmra1hohiZs',
 '0NyTH17EcMRIBy6Qmwx0',


In [ ]:
qid[1]

{'exam_name': '2017S_FE_AM_Question.pdf',
 'answers': ['MTBF of a system decreases and MTTR of a system increases through remote \nmaintenance.',
  'MTBF of a system increases as the number of device types that constitutes the system \nincreases.',
  'MTBF of a system increases through preventive maintenance.',
  'MTTR increases because of functions such as an error log or an instruction trace.'],
 'question_number': 17,
 'question': 'Q17. Which of the following is an appropriate description concerning MTBF and MTTR?'}

In [ ]:
# ทำความสะอาดข้อความ
import re

def clean_question(question):
  question = re.sub(r'^Q\d+\.\s', '', question)
  question = question.replace('\n', ' ')
  question = re.sub(r'\s+', ' ', question)
  return question.strip()

In [ ]:
import pandas as pd
from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-MiniLM-L6-V2')

def data_to_list(key):
  result = []
  for item in qid:
    result.append(item[key])
  return result

questions = data_to_list('question')
answers = data_to_list('answers')
exam_name = data_to_list('exam_name')
question_number = data_to_list('question_number')

questions = [clean_question(question) for question in questions]
embedding = [model.encode(question, convert_to_tensor=True) for question in questions]

df = pd.DataFrame({
    'exam_name': exam_name,
    'question_number': questions,
    'question': questions,
    'answers': answers,
    'embedding vector': embedding
})

In [ ]:
df.head()

exam_name  \
0     2012S_IP_Question.pdf   
1  2017S_FE_AM_Question.pdf   
2    2023A_IP_Questions.pdf   
3    2023A_IP_Questions.pdf   
4  2018A_FE_AM_Question.pdf   

                                     question_number  \
0  Which of the following is an appropriate descr...   
1  Which of the following is an appropriate descr...   
2  Which of the following is an appropr iate purp...   
3  Among the requirements for the design of scree...   
4  Which of the following is an appropriate cost ...   

                                            question  \
0  Which of the following is an appropriate descr...   
1  Which of the following is an appropriate descr...   
2  Which of the following is an appropr iate purp...   
3  Among the requirements for the design of scree...   
4  Which of the following is an appropriate cost ...   

                                             answers  \
0  [Since more files are accessed simultaneously ...   
1  [MTBF of a system decreases and MTTR of a syst...   
2  [To provide basic hardware control to su ch eq...   
3               [A, B, C, A, B, D, A, C, D, B, C, D]   
4  [Analogous estimating, Bottom-up estimating, F...   

                                    embedding vector  
0  [tensor(-0.0075), tensor(-0.0050), tensor(-0.0...  
1  [tensor(-0.0667), tensor(-0.0048), tensor(0.02...  
2  [tensor(-0.1071), tensor(0.0375), tensor(-0.02...  
3  [tensor(-0.0224), tensor(0.0057), tensor(-0.00...  
4  [tensor(-0.0650), tensor(-0.0026), tensor(-0.0...

## **K-means clustering**

In [ ]:
from sklearn.metrics import silhouette_score
import numpy as np
from sklearn.cluster import KMeans
from matplotlib import pyplot as plt

def Silihouette(embedding, max_k=15):
  s = []
  for k in range(3,max_k+1):
    kmeans = KMeans(n_clusters=k, init='k-means++')
    kmeans.fit(embedding)
    labels = kmeans.labels_
    centroids = kmeans.cluster_centers_
    silhouette_avg = silhouette_score(embedding, labels)
    s.append(silhouette_avg)

    print("Silhouette Coefficient for k == %s: %s" % (k, round(silhouette_score(embedding, kmeans.labels_), 4)))

Silihouette(embedding)

Silhouette Coefficient for k == 3: 0.0295
Silhouette Coefficient for k == 4: 0.0291
Silhouette Coefficient for k == 5: 0.0302
Silhouette Coefficient for k == 6: 0.0319
Silhouette Coefficient for k == 7: 0.0343
Silhouette Coefficient for k == 8: 0.0259
Silhouette Coefficient for k == 9: 0.0269
Silhouette Coefficient for k == 10: 0.0326
Silhouette Coefficient for k == 11: 0.0312
Silhouette Coefficient for k == 12: 0.0299
Silhouette Coefficient for k == 13: 0.0307
Silhouette Coefficient for k == 14: 0.0245
Silhouette Coefficient for k == 15: 0.0318


In [ ]:
k = 7
kmeans = KMeans(n_clusters=k)
question_clusters = kmeans.fit_predict(embedding)

df_cluster = pd.DataFrame({'question ID': id, 'cluster': question_clusters})

In [ ]:
df_cluster['cluster'].value_counts()

cluster
1    898
5    808
4    665
0    639
6    579
3    449
2    372
Name: count, dtype: int64

In [ ]:
df_cluster.head()

question ID  cluster
0  00BIC4wIflXSsvOO7MBa        6
1  00Q6RDxYvNgcPCwg2tXg        4
2  00bkasubJySUQFp0zvlu        0
3  012H0gVUcCApoodLY5gD        4
4  016FY0dqdVBGLbZ4dNG5        0

In [ ]:
def add_data_to_firestore(qid, cluster):
    try:
      db.collection('Cluster_Test3').add({
          'Cluster Name': cluster,
          'QuestionsID': qid,
        # 'correct_answer': item['correct_answer']
    })
    except Exception as e:
      print(e)
      print(item)

for i in range(8):
  add_data_to_firestore(df_cluster[df_cluster["cluster"]==i]['question ID'].tolist(), i)

## **Embedding Cluster**

In [ ]:
clusters_data = db.collection('Cluster_Test2').stream()
clusters_id = [id.id for id in clusters_data]
cluster_questions = [doc.to_dict().get("field3") for doc in clusters_data]

In [ ]:
clusters = []
for cluster in cluster_questions:
  cluster_data = [
      db.collection('exams').document(qid).get().to_dict().get('question')
  for qid in cluster
                  ]

  clusters.append(cluster_data)


In [ ]:
from collections import Counter
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
import nltk
import re

def clean_question(question):
  question = re.sub(r'^Q\d+\.\s', '', question)
  question = question.replace('\n', ' ')
  question = re.sub(r'\d+', ' ', question)
  question = re.sub(r'\s+', ' ', question)
  return question.strip()

nltk.download('wordnet')
nltk.download('omw-1.4')

nltk.download('stopwords')
stop_words = set(stopwords.words('english'))
stop_words.add('following')

lemmatizer = WordNetLemmatizer()

wordclouds = []
for cluster in clusters:
  texts = [clean_question(text) for text in cluster]
  texts = ' '.join(texts).lower()
  print(texts)
  words = re.findall(r'\b\w+\b', texts)

  lemmatized_words = [lemmatizer.lemmatize(word) for word in words]

  filtered_words = [word for word in lemmatized_words if word not in stop_words]

  word_counts = Counter(filtered_words)
  word_list = word_counts.most_common()
  wordclouds.append(word_list)


[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


which of the following is an appropriate meas ure of facility management that maintains and protects facilities and equi pment of information systems when information processing systems are classified by their pr ocessing methods as shown in the figure below which of the follow ing is an explanation of a horizontal load distribution system which of the following correspond s to information barrier free which of the following is an appropriate measure of facility ma nagement that maintains and protects facilities and equipm ent of an information system which of the following is the most appropriate information fo r a router to determine the destination of an incoming packet in order to evaluate groupw are installed an information systems department sends a questionnaire to employees once every si x months the questionnaire has eight evaluation items including the transmission sp eed level of sharing and recentness of information employees evaluate each item on a scale of one to ten whic

In [ ]:
wordclouds[5][:20][1][0]

'file'

In [ ]:
import re

def clean_question(question):
  question = re.sub(r'^Q\d+\.\s', '', question)
  question = question.replace('\n', ' ')
  question = re.sub(r'\s+', ' ', question)
  return question.strip()

In [ ]:
from sentence_transformers import SentenceTransformer
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np

model = SentenceTransformer('all-MiniLM-L6-V2')

cluster_embedding = []
for texts in clusters:
  vectorizer = TfidfVectorizer()
  tfidf_matrix = vectorizer.fit_transform(texts).toarray()
  tfidf_scores = np.mean(tfidf_matrix, axis=1)

  texts = [clean_question(text) for text in texts]
  embedding = model.encode(texts)

  weighted_embedding = np.average(embedding, weights=tfidf_scores, axis=0)
  cluster_embedding.append(weighted_embedding)

In [ ]:
cluster_embedding[0]

array([-0.03023302,  0.03626058, -0.03818108, -0.04308791,  0.00446501,
        0.00517958,  0.07721815,  0.02295023,  0.02844278,  0.01512303,
        0.03080263,  0.02798415,  0.04398263, -0.01027093, -0.01140232,
       -0.0181318 ,  0.01644742, -0.03872017, -0.02830488, -0.01060611])

In [ ]:
def format_wordcloud(wordcloud):
    return [{"word": word, "count": count} for word, count in wordcloud]

def add_data_to_firestore(cid,vector,questions,wordcloud):
    try:
      db.collection('Cluster_Test2').document(cid).set({
          'Embedding vector': vector,
          'Questions': questions,
          'Wordcloud': format_wordcloud(wordcloud)
    })
    except Exception as e:
      print(e)

for i in range(11):
  add_data_to_firestore(clusters_id[i],
                        cluster_embedding[i].tolist(),
                        cluster_questions[i],
                        wordclouds[i][:20]
                        )

# **fix questions**

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
from firebase_admin import firestore, credentials
import firebase_admin

cred = credentials.Certificate('/content/drive/MyDrive/itpe_exams/exam-matching-firebase-adminsdk-hdm65-231e235b83.json')
firebase_admin.initialize_app(cred)

db = firestore.client()

In [ ]:
def remove_question_number(text):

    corrected_text = re.sub(r"Q\d+\.", "", text)
    return corrected_text

def update_firestore_data():
    docs = db.collection('exams').stream()

    for doc in docs:
        data = doc.to_dict()
        updated_data = {}
        is_updated = False

        if 'question' in data:
            original_question = data['question']
            cleaned_question = remove_question_number(original_question)

            if cleaned_question != original_question:
                updated_data['question'] = cleaned_question
                is_updated = True

        if is_updated:
            db.collection('exams').document(doc.id).update(updated_data)
            print(f"Updated document {doc.id}: {updated_data}")

update_firestore_data()

# **Delete data**

In [ ]:
db = firestore.client()

docs = db.collection('Cluster_Test2').stream()
cids = [doc.id for doc in docs]

delete_ids = []
for qid in cids:
  doc = db.collection('Cluster_Test2').document(qid).get().to_dict().get('Questions')
  for id in doc:
    data = db.collection('exams').document(id).get()
    if not data.exists:
      doc_ref = db.collection('Cluster_Test2').document(qid)

      print(id)
      doc_ref.update({
              'Questions': firestore.ArrayRemove([id])
      })

      delete_ids.append(id)

print(len(delete_ids))

2yWT5izFfZIWhEzEME63
LNYWsLPuvlqFGNEcJaU8
QNXTPG7Npbjxkxr5dNKt
RdXdxH6UTuDLFBiq4G89
TxXUJEsT2j63kOvv5hXX
UNgH7KJ34uN1OP2peQd8
X9Qgap6zvwaovQXOFPv9
YojRXCUY2561fnkZKlg9
YxoQW6g5yaD7MVnk3hcc
beVvljV0sO3uUzBJDXup
e8tsjkAzVdH7YKuNhif7
gCLgo0cNoJhGphqtnV96
ggbNZ6TsoLHLkCglumfV
j7Ct5uNytenKVQR6OjSP
ob7mXPxuiQn3Vct88ulI
ojM9fZ5IZBXnmqHhAKSe
rcyiv9Os2obLsPYjL7Ai
u2MgwZyNJc4utg4mO6Mu
ujs2p7mYzAMOr4uaYP6M
wQcWDWhI2PwxD7w8V8bt
xZRtZ7IxblchOdHjoVGA
yHnHTVIcL53K90z0nLcB
zgpzPtDEshCAaBJxlkXj
5ZPglDIB7YdRyskFtF52
5v1mMXhRZuFRIJ9QaItF
7khtrKKFUutcjBVBIkMX
8reNQuazU82GYds5ZDQD
9x3z2PDF49lsYCDk9hu4
AR0IxxS6H48JuQqtA7mH
B08qopJIZJxF4WMreu92
BY9yL1FTObk54adLN2xa
BkwUeHsH86tJd9bbQ5Bw
Cdduylc2BNZiU9qTM49S
Cw6gDWivqla383yJarkU
DiwS7PbOgFDnLPSyJNa7
ECSdgnuhd6NsnVjjZBjU
EOD8aLox0UfRarpRfGuo
EfBf0NUKUNRzZe80U0ri
FNrHBYJUY8eS2KxSQxvr
HNDztapYYWsA620h4xq3
HOv3ieI20qvGXiZiOpKh
Hp56vpJJEvpGT8aqmm7D
HpZbzdHSKSlAa1qvzivY
HvX0ti3ldfcLiRNQ5s5Q
JAjX5whCOWPXnckywwoj
K23Vm6bRGt3ymcPcwVbd
LShBZheDHe5TQXZzRn2T
M7Z3VwPCk0hKl

In [ ]:
import re
from nltk.util import ngrams
from collections import defaultdict

# ฟังก์ชันช่วยสำหรับการทำความสะอาดคำถาม
def clean_text(text):
  text = re.sub(r'^Q\d+\.\s', '', text)  # ลบ Q<number>.
  text = re.sub(r'\s+', ' ', text).strip()  # ลบช่องว่างเกิน
  return text

# ฟังก์ชันตรวจสอบว่าคำถามซ้ำกันหรือไม่
def is_similar(question1, question2, word_difference_threshold=3):
  def compare_direction(words1, words2):
      i, j = 0, 0  # ตัวชี้ index สำหรับคำทั้งสองชุด
      while i < len(words1) and j < len(words2):
          if words1[i] == words2[j]:  # ถ้าคำตรงกัน
              i += 1
              j += 1
          else:
              # ลองนำคำจากฝั่ง `words1` มาต่อกัน
              if i + 1 < len(words1) and words1[i] + words1[i + 1] == words2[j]:
                  i += 2  # ข้ามคำที่ concat ไป
                  j += 1
              # ลองนำคำจากฝั่ง `words2` มาต่อกัน
              elif j + 1 < len(words2) and words1[i] == (words2[j] + words2[j + 1]):
                  i += 1
                  j += 2  # ข้ามคำที่ concat ไป
              else:
                  return False  # ถ้าไม่ตรงและ concat แล้วไม่ตรงกัน
      return i == len(words1) and j == len(words2)  # ต้องจบทั้งสองคำถามพร้อมกัน

  words1 = question1.split()
  words2 = question2.split()

  # ถ้าความยาวต่างกันเกิน threshold ให้ข้าม
  if abs(len(words1) - len(words2)) > word_difference_threshold:
      return False

  # เปรียบเทียบทั้งสองทิศทาง
  return compare_direction(words1, words2)


# โหลดคำถามจาก Firestore
docs = db.collection('exams').stream()
qids = [doc.id for doc in docs]

questions = {}  # เก็บคำถามและ id
potential_duplicates = defaultdict(list)  # เก็บ id ของคำถามที่อาจซ้ำ

# เริ่มกระบวนการ
for qid in qids:
    doc_snapshot = db.collection('exams').document(qid).get()
    if doc_snapshot.exists:
        data = doc_snapshot.to_dict()
        question = clean_text(data.get("question", ""))

        if question:
            is_duplicate = False
            # เปรียบเทียบกับคำถามที่มีอยู่ใน `questions`
            for existing_question, existing_id in questions.items():
                if is_similar(question, existing_question):  # ใช้ฟังก์ชันเปรียบเทียบคำ
                    is_duplicate = True
                    potential_duplicates[existing_id].append(qid)  # บันทึก ID ของคำถามที่อาจซ้ำ

            # ถ้าคำถามไม่ซ้ำ ให้เพิ่มลงใน `questions`
            if not is_duplicate:
                questions[question] = qid

# แสดงผลคำถามที่อาจซ้ำ
for original_id, duplicate_ids in potential_duplicates.items():
    print(f"Original ID: {original_id} | Duplicate IDs: {duplicate_ids}")


Original ID: 0X8YQ12HO84YhoskTnWl | Duplicate IDs: ['5R2LXlOfzvFSR5KiSsg1']
Original ID: 2x73shcH4ASjwA4csseJ | Duplicate IDs: ['6nE5M1kgqINJ43tOoiG6']
Original ID: 2AeNTYEh2zmBU2ZLCyaA | Duplicate IDs: ['8reNQuazU82GYds5ZDQD']
Original ID: 0crKnQukJj78tKHH5iZN | Duplicate IDs: ['99OeFYwZfHhIZMC3fbSz']
Original ID: 44AGkwvxbWeYOnbF8ANG | Duplicate IDs: ['AR0IxxS6H48JuQqtA7mH']
Original ID: 7U2ovoiZTh59lCavy7LI | Duplicate IDs: ['B08qopJIZJxF4WMreu92', 'EfBf0NUKUNRzZe80U0ri']
Original ID: 2Z17zgBc6kGprQCoQh7A | Duplicate IDs: ['BkwUeHsH86tJd9bbQ5Bw']
Original ID: 3yqzSEJbrKyOJut6QnAP | Duplicate IDs: ['Cdduylc2BNZiU9qTM49S']
Original ID: 2zVvxmtI9tgGCJkF3mNF | Duplicate IDs: ['DRKppkoA9TjgrIzqz9lH']
Original ID: BCOb2WXRxKFMd9y4dOCd | Duplicate IDs: ['FmQBEnDOpj5FTkbzDNCg']
Original ID: AoBHlk7NWzNcFSJCsi8W | Duplicate IDs: ['Hp56vpJJEvpGT8aqmm7D', 'SWLkxnZ2FZC9hUk9wwy3']
Original ID: H5hwu1m1zRChat1eBBim | Duplicate IDs: ['HsDZ9U6Y7l5qr6AkIChC']
Original ID: BSnmw57itJCMnjRNqd7y | Dupl

In [ ]:
len(qids) - len(potential_duplicates)

4010

In [ ]:
# ลบ id ตัวหลัง (id2) ของแต่ละคู่ใน duplicate_couples
for id1, id2 in potential_duplicates.items():
    try:
        # ลบเอกสารที่มี id = id2
        for id in id2:
          db.collection('exams').document(id).delete()
        print(f"Document {id2} deleted successfully (paired with {id1}).")
    except Exception as e:
        print(f"An error occurred while deleting document {id2}: {e}")


Document ['5R2LXlOfzvFSR5KiSsg1'] deleted successfully (paired with 0X8YQ12HO84YhoskTnWl).
Document ['6nE5M1kgqINJ43tOoiG6'] deleted successfully (paired with 2x73shcH4ASjwA4csseJ).
Document ['8reNQuazU82GYds5ZDQD'] deleted successfully (paired with 2AeNTYEh2zmBU2ZLCyaA).
Document ['99OeFYwZfHhIZMC3fbSz'] deleted successfully (paired with 0crKnQukJj78tKHH5iZN).
Document ['AR0IxxS6H48JuQqtA7mH'] deleted successfully (paired with 44AGkwvxbWeYOnbF8ANG).
Document ['B08qopJIZJxF4WMreu92', 'EfBf0NUKUNRzZe80U0ri'] deleted successfully (paired with 7U2ovoiZTh59lCavy7LI).
Document ['BkwUeHsH86tJd9bbQ5Bw'] deleted successfully (paired with 2Z17zgBc6kGprQCoQh7A).
Document ['Cdduylc2BNZiU9qTM49S'] deleted successfully (paired with 3yqzSEJbrKyOJut6QnAP).
Document ['DRKppkoA9TjgrIzqz9lH'] deleted successfully (paired with 2zVvxmtI9tgGCJkF3mNF).
Document ['FmQBEnDOpj5FTkbzDNCg'] deleted successfully (paired with BCOb2WXRxKFMd9y4dOCd).
Document ['Hp56vpJJEvpGT8aqmm7D', 'SWLkxnZ2FZC9hUk9wwy3'] deleted 

In [ ]:
import re

# กำหนดชื่อ collection ที่ต้องการ
collection_name = "exams"

# ดึงข้อมูลทั้งหมดใน collection
docs = db.collection(collection_name).stream()

# เก็บค่าของ question และ id
questions = {}
duplicate_couples = []

for doc in docs:
    data = doc.to_dict()
    question = data.get("question")
    question = re.sub(r'^Q\d+\.\s', '', question)
    if question:
        # ตรวจสอบว่ามีค่า question ซ้ำหรือไม่
        if question in questions:
            duplicate_couples.append((questions[question], doc.id))  # สร้างคู่ id ที่ซ้ำกัน
        else:
            questions[question] = doc.id

print("Duplicate question pairs (id1, id2):")
for pair in duplicate_couples:
    print(pair)


Duplicate question pairs (id1, id2):
('00Q6RDxYvNgcPCwg2tXg', '4rv04xALeCiurM9WzKhZ')
('4jUBy9RsanyRguRcbhh2', '5ZPglDIB7YdRyskFtF52')
('4DpM7j6xYLupJqAvzRhT', '5v1mMXhRZuFRIJ9QaItF')
('0UDEE6WHyPeBytyePhd8', '9iPLgsKwyTrvkcj6RgZy')
('43fSqmc3VCzZ6gUBYKdf', 'A3dLLBM7btz7XOP5oF1T')
('1xhfINP9HMmST84RLbi8', 'Cw6gDWivqla383yJarkU')
('6OqItk1vdvsL5oYpRab7', 'EOD8aLox0UfRarpRfGuo')
('0w57eCvEtsaPm4xoYrz8', 'FNrHBYJUY8eS2KxSQxvr')
('9lSoEIpYaMIs9zeVRBuP', 'Fjh8XtMZfJlLF57slzqe')
('9jq9b7vMzKPBr5M5i3KJ', 'HNDztapYYWsA620h4xq3')
('ErVPzuPQtKGjQZm4QcEG', 'HOv3ieI20qvGXiZiOpKh')
('B95fjaD2aoEEnPvqkZWW', 'HvX0ti3ldfcLiRNQ5s5Q')
('2cp0FXnKQMdmPn4Pzxqs', 'KBab8NTAzePyRpj1QrxZ')
('8eULXUMiQLY68SVJ25yu', 'KZNLC1hAOZWWn5aQKk4s')
('2s2r6JMsaYLoEpsfQcg1', 'LNYWsLPuvlqFGNEcJaU8')
('DEb1LKJLSjv1C6u0HQd4', 'N50TfydD0GUzk5DMTFhg')
('NYxCrmHiCeQmKx3cSrKR', 'O1uqOZSpUQYhpB2kSTEv')
('708t39I5hYsnqrBP1vTd', 'OscxGez0VB3C3fsLgcAs')
('35v1Ja3BQJS7r8jO5uoD', 'PK1Q6EslNKTyVuwHIeeL')
('CMnNianNWJ4uDH70TfTL', 'Pgh4WN

# **Key words of each cluster**

In [ ]:
!pip install keybert

In [ ]:
cluster_ids = db.collection('Cluster_Test2').stream()
cluster_ids = [id.id for id in cluster_ids]

In [ ]:
cluster_ids

['3KENaUxsMffy66kIeyRo',
 '4bvU9CcZQZW1AvdQsW0q',
 'DaigQLrCFTQIaJkHugk8',
 'JyAOgqXMsixrbCx8Ef8P',
 'MZkhebzSpKiJ6363slZj',
 'Yf3bxcNBrgnhT7iwmOll',
 'bgpS1q8VFaBEhjURqrbq',
 'hQ9SdnyeWRWty5p8KbUB',
 'jDuobXqOoilPjoV4m6hK',
 'nZpOEwlCeuLMMzo36Wao',
 'tsDEsmDFauRhUrSXZJur']

In [ ]:
questions_ids = []
for id in cluster_ids:
  cluster_data = db.collection('Cluster_Test2').document(id).get().to_dict().get('Questions')
  questions_ids.append(cluster_data)

In [ ]:
len(questions_ids[0])

254

In [ ]:
import re

def clean_question(question):
  question = re.sub(r'\bQ\d+\b', '', question, flags=re.MULTILINE)
  question = question.replace('\n', '')
  question = re.sub(r'\s+', ' ', question)
  return question.strip()

In [ ]:
doc_each_cluster = []
for cluster in questions_ids:
  text = ''
  for qid in cluster:
    question = db.collection('exams').document(qid).get().to_dict().get('question')
    text += " " + question
  text = clean_question(text)
  doc_each_cluster.append(text)

In [ ]:
# doc_each_cluster = [clean_question(doc) for doc in doc_each_cluster]
print(doc_each_cluster[0])

. Which of the following is an appropriate meas ure of facility management that maintains and protects facilities and equi pment of information systems? . When information processing systems are classified by their pr ocessing methods as shown in the figure below, which of the follow ing is an explanation of a horizontal load distribution system? . Which of the following correspond s to information barrier-free? . Which of the following is an appropriate measure of facility ma nagement that maintains and protects facilities and equipm ent of an information system? . Which of the following is the most appropriate information fo r a router to determine the destination of an incoming packet? . In order to evaluate groupw are installed, an information systems department sends a questionnaire to employees once every si x months. The questionnaire has eight evaluation items including the transmission sp eed, level of sharing, and recentness of information. Employees evaluate each item on a s

In [ ]:
from keybert import KeyBERT

kw_model = KeyBERT()
keywords_each_cluster = {}

for i,text in enumerate(doc_each_cluster):
  keywords = kw_model.extract_keywords(text,
                                      keyphrase_ngram_range=(1,2),
                                      highlight=True,
                                      stop_words='english',
                                      diversity=0.7,
                                      top_n=10)
  keywords_each_cluster[cluster_ids[i]] = keywords
keywords

Which of the following is an appropriate meas ure of facility management that maintains and protects facilities and
equi pment of information systems When information processing are classified by their pr ocessing methods as shown 
in the figure below which of the follow ing is an explanation of horizontal load distribution system Which of the 
following correspond to information barrier free Which of the following is an appropriate measure of facility ma 
nagement that maintains and protects facilities and equipm ent of an information system Which of the following is 
the most appropriate information fo router to determine the destination of an incoming packet In order to evaluate 
groupw are installed an information systems department sends questionnaire to employees once every si months The 
questionnaire has eight evaluation items including the transmission sp eed level of sharing and recentness of 
information Employees evaluate each item on scale of one to ten Which of the following is an appropriate chart or 
diagra for representing this evaluation result Which of the following is the coding sche me that can encode large 
amount of information into small area nd has an error correc tion function that enables the code to be read out 
correctly ev en when the code cannot be partially read out Concerning information security which of the following 
is an event where availability is compromised When information security management is based on the PDCA cycle which
of the following corresponds to When information security management is based on the PDCA cycle which of the 
following corresponds to Which of the following is the security attack that is used for an illegal attempt to 
manipulate the people of an organization into divul ging the password and confidential information under the 
pretext of an emergency Which of the following is an officer whose pr imary responsibility is the security of 
company information and data Which of the following is used to confirm that there is no falsificat ion of the 
content of an mail Which of the following protocols can be used to access mail messages that are stored on remote 
and possibly shared mail serv er and thereby are manipulated from desktop computer at home workstation at the 
office and notebook computer while traveling without the need to transfer messages back and forth between these 
computers Which of the following is performed in the PLAN phase of PDCA Plan Do Check Act model applied to an ISMS 
Information Security Management System process Which of the following is an explanati on of the timestamp service 
in information security Among the following lists consis ting of the information security terms availability 
integrity confidentiality and vulnerability wh ich is complete list of properties of information that information 
security is to preserve Which of the following is security incide nt categorized as being caused by physical threat
Among the management functions for service support which of the following is the process of identifying all IT 
assets such as hardwa re and software and creating and maintaining an up to date record of those IT assets 
including related documentation or such other information Which of the following can provide accessible linkage 
between information items represented in text still images video sound music and other forms so that associated 
information can be reached by visiting one link after another From the viewpoint of considerat ion for recipients 
of mail hich of the following is the most appropriate example of mail transmission When sender from domain sends an
mail to recipient in domain which of the following is used by the mail server in domain for authenticating the 
sender Which of the following is socio economic disparit or inequality that is caused by the differences in skills 
or opportunities to use ICT Information and Communication Technologies such as PC and the Internet In company 
accounting department new fin

Which of the following is an appropr iate purpose of in stalling groupware Which of the following is an appropriate
cost estimation techn ique that uses parametric models to create an objective estimate based on each element si ze 
and the complexity of the system number of input files screens etc to be uilt Which of the following activities 
aims at the maintenance and improvement of the service level through monitoring and review of the service status in
order to implement the terms of agreement of an SLA Which of the following can be made possible by usin digital 
signature in commerce In IT service management which of the fo llowing is the most appropriate functional 
organization that provides single point of cont act and tries to rapidly restore normal service operations to users
Which of the following SQL statements corr esponds to the projection operation of the relational algebra that can 
extract only the column Continent from the table Country and eliminate duplicates from the records returned Country
Name Continent Canada North America Malaysia Asia Malawi Africa Brazil South America Germany Europe China Asia 
survey into the amount of pocket money is conducted at three schools When the consolidated results of the survey 
are used to calculate the average pocket money per student for all the students of the three schools which of the 
following is the expression that is entered into cell C5 Number of students Average of pocket money per student 
School 150 250 School 250 850 School 60 530 Average of pocket money per student Which of the following is the 
standard used to desc ribe the look and formatting of markup language documents such as HTML and XHTML PEST 
analysis is used for analyzing the external environment in determining business strategy What are the external 
environmental factors the PEST analysis analyzes When an attacker makes an unauthorized intr usion into computer 
the attacker sometimes changes program or settings in the computer in order to make further intrusions into the 
computer easier Which of the following is the most appropriate term to express the method used by the attacker for 
further intrusions into the computer Which of the following is framework that desc ribes collection of best 
practices of IT service management When computerization is promoted which of the following is an appropriate point 
to be noted In the process of creating animation which of the following is used to incorporate the natural movement
of objects humans and animals by using sensors and video cameras In process that aims to produce ideal tec hnology 
technology follo ws an evolutionary process that progresses from the introduction stage growth stage matur ity 
stage and decline stage Then it transitions to the next technolog ical phase Which of the following is used to 
represent this technol ogical evolution process When 12 point character is displayed in bitmap on 96 dpi display 
screen how many dots are used for the height of square font Her point is 72 inch IT control is classified into 
general control and application control concerning IT General control refers to the control activities fo 
guaranteeing the environment in which each application control works effectively Applic ation control refers to the
control activities for ensuring that all business operation approved in the system for managing business operations
are processed and recorded appr opriately Among the descriptions concerning IT control activities which of the foll
owing can be regarded as general control Which of the following is term that shows the amo unt of work that is 
processed per unit of time by computer system Which of the following is the most appr opriate design policy for an 
output form Which of the following is the purpose of DoS attack against server Which of the following is an 
appropriate reason for using re al time OS in an embedded system During business system development it is eff 
ective to collect the meaning and

Which of the following is an appropriate expl anation of 3C analysis that is used to analyze business environment 
In the development of consolidated acc ounting system functional requirements and non functional requirements were 
classified as shown in the table below Which of the following is the appropriate requireme nt to be inserted into 
blank Functional requirements Non functional requirements Accounting be performed in accordance with international 
accounting standards Confirmation of acc ount closing results is performed by the accounting department manager 
Records are obtaine for all account closing processes All batch processes are completed within hours All data to be
kept is encrypted Which of the following is the most appropriate expl anation of multimedia authoring tool Which of
the following is an expl anation of busin ess process model Which of the following is the most appropriate expl 
anation of dual system Which of the following is the development model whe re trial model or pilot unit is 
developed at an early stage of system development that users can verify their requirements in tangible manner Which
of the following is an expl anation of recursive call çWhich of the following is an appropriate expl anation of 
external design and internal design Which of the following corresponds to an example non functional requirements 
The processes of system development include system requirements definition systems architecture design system 
integration testing and software acceptance Which of the following is an activity that is performed in system 
requirements definition 21 When system development progresses in the sequence of system requirements definition 
external design internal design and rogramming which of the following is the most appropriate phase for defining 
the layout of screens and the format of forms In software life cycle that proceeds in order of planning process 
requirements process development process and maintenance pro cess which of the following is an appropriate activity
to be performed at the stage of the planning process Which of the following is work that is performed when 
nonfunctional requirements are defined Which of the following is the appropriate expl anation of the DFD that is 
created when business process is analyzed Which of the following is an appropriate expl anation of commercial 
database service Which of the following is an appropriate purpose of defining business requirements in system 
development Which of the following is an appropriate expl anation of the characteristics and usage of an optical 
disk Which of the following is an expl anation of SCM Supply Chain anagement Which of the following is the most 
appropriate expl anation of TCO Total Cost of Ownership which is major factor when any purcha sing decision is made
for system Which of the following is an appropriate expl anation of the POS terminal or POS cash register in 
supermarket and other such places Which of the following is the appropriate ex planation of master schedule in 
system development project where pr ocesses from requirements definition to installation are performed Which of the
following is the situation where an im provement can be expected by installing an MRP Material Requirements 
Planning system Which of the following is an expl anation of Business Intelligen ce BI Which of the following is 
the development model whe re trial system is developed at an early stage of system development so that users can 
verify their requirements in tangible manner Which of the following is the term that means the process of modifying
some of the functions of software package on the basis of use environments and requirements Which of the following 
is an expl anation of the on functional requirements definition According to the ISO 9000 family quality is define 
as the degree to which set of inherent characteristics fulfills requirements hen products are evaluated on the 
basis of this definition whic

In commerce such as mail order business th ere is risk that dealers or users are damaged by falsifying spoofing and
repudia tion at the time of sa les order or purchase order Which of the following is an appr opriate security 
technology can cope well with all of these three threats Which of the following is the software development process
that aims to achieve high degree of complet ion of system by dividing the system into some subsystems and repeating
the development cycle for each subsystem in consideration of minimizing the risk in each cycle Among the 
descriptions through concerning the measures for risk reduction to be considered when new product is developed 
which the following is the list that contains all appropriate measures for reducing qual ity related risks 
Developing product by using stable technology Purchasing insurance against development delays Creating prototype of
the product Mr encrypts message to be sent to Mr using an asymmetric key encryption method so that only Mr can 
decrypt the message Which of the following is are th private key used to decrypt the message Which of the following
is regarded as risk sharing or risk transfer Among the descriptions through concerning the measures for risk 
treatment to be considered when new product is developed which of the following is the list that contains all and 
only appr opriate measures for reduc ing quality related risks Developing product by using stable technology 
Purchasing insurance agai nst development delays Creating prototype of the product In order to reduce the risk of 
unauthorized entry nto the server room where computer system is operating the decision is made not to in dicate the
installation location of the computers Which of the following is the appropria te management that corresponds to 
this measure Mr is appointed as the project manager of project to add functions to the finance system He gets risk 
checklist that was used in past project in order to create new risk checklist for the project Whic of the following
is an appropriate description concerning the risk checklist Mr is instructed by Mr to examine if there are any more
risks with larg impact other than point of Status of Project Which of the points through of Status of Project has 
risk with the largest impact There are negative and positive risks in project Among the reatment of risks in 
scheduling which of the followi ng corresponds to treatment positive risk Which of the following is not an appropr 
iate security cont rol concerning human resources as security risk in ISMS Mr creates an mail for sending request 
for partic ipation in the questionnaire survey to employees so that the instructions given by his manager can be 
accomplished Which of the following is the approp riate description to be inserted into blank In order to improve 
the working environment sati sfaction survey is to be conducted All the employees are in the scope of he survey The
deadline is the end of next month We look for ward to your cooperation and support Please contact Mr of the HR 
department for any questions about this survey When Mr sends his confidential message to Mr by using public key 
cryptography as shown in the figure below which of the following is the appropriate key used for encryption Mr Mr 
NetworkDecrypt with Mr private keyEncrypt with key will transfer next month will transfer next month nd359fxj47ac 
nd359fxj47ac Mr decides to arrange the questionnaires according to the instructions that are given by his manager 
Which of the following is the appr opriate method for arranging questionnaires In development project for system 
there is plan to create 36 programs with the same size It was first planned to assign only Mr who can create six 
programs per week but the plan was changed and it was decided to assign two people Mr and Mr who has half the 
productivity of Mr When the cost per week for Mr and Mr is 300 thousand yen and 200 thousand yen resp ectively how 
much is the chang

Company summarized the results of positioning analysis of its marketing power in relation to competitors into the 
table as sh own below In the table is the lowest score and is the highest score Where does Company rank the top 
Weight Company Company Company Company Price Product quality Brand name Selling power Which of the following is an 
appropriate xplanation of the table obtained when the SELECT statement shown below is executed SELECT Products 
Product_code SUM Unit_price Sales_volume FROM Products Sales WHERE Products Product_code Sales Product_code GROUP 
BY Products Product_code ORDER BY SUM Unit_price Sales_volume Products Sales Product_code Product_name Unit_price 
Cu stomer Product_code Sales_volume A5023 Shampoo 500 Company A5023 100 A5025 Rinse 400 Store A5023 150 A5027 Soap 
100 Company A5025 120 Company A5027 100 Store A5027 160 Which of the following is direct result of SQL injection to
company web server company purchased the enterprise license of software that can be used for 100 PCs and then 
installed it on th ose PCs Which of the following is an action that complies with the license agreement Which of 
the following is the most appropriate terminology for referring to method that uses AI IoT and other such IT for 
personnel related work such as personnel evaluations and recruitment with aims including the imp rovement of 
company personnel functions and achieving reform in working styles Which of the following is the most appropr iate 
for conveying company belief in management and its sense of values to employees customers and society Which of the 
following is appropriate as the evaluation ax es in PPM that are used in optimizing the allocation of management 
resources across multiple businesses in company An attacker calls corporate help desk ma squerading as an employee 
who has forgotten his password The help desk staff resets the password to the company default password1 The 
attacker then uses this password to acc ess the company network and information on the server What is this type of 
attack called When company own product is analyzed by using SWOT analysis which of the following is classified as 
an external factor Retail company is teaching the general distributi on process for food products in an easily 
understandable manner at elementary schools near the company distribution center Which of the foll owing is an idea
behind these activities by company company is aiming to analyze the data that is acc umulated in an information 
system and use such data in business operations However progress is not made because of the insufficient experience
of employees Which of the following is the most appropriate activity that should be performed with higher priority 
in order to achieve the objective Which of the following is an approach of mutually ranting the right to execute 
the patents owned by each company as way of introduci ng external technologies The figure below shows each break 
even point of Company and Company Which of the following is an appropri ate description concerning the benefit risk
analysis of the two companies Income Income Cost CostIncome cost Break even point Income cost Break even point 
Sales Sales 0100 100 100 10070 30Company Company Which of the following is term that means that the de velopment 
and operation of system is farmed out to an overseas company or an overseas subsidiary In order to make good use of
IT to implement the bu siness strategy of company which of the following is the most appropriate point to 
considered when an information strategy is created company is planning to transfer file containing accounting data 
created with PC in text format to the company wide acc ounting system managed by the information systems department
Which of the followi ng is the most appropriate item which should be checked in advance When ten mail messages are 
sent successively from Company to Company they may arrive at Company in different order from the order they are 
sent

...

Which of the following is protocol used by the ping command in order to verify that the communication link between 
source and de stination is working in the TCP IP network environment There is network that is divided into thr ee 
segments namely an external segment DMZ and an internal segment by one fire wall In this network service for users 
is published on the Internet using system compri sing web server and database server that contains critical data 
Which of the following is the most appropriate server installation method for protecting critical da ta from 
unauthorized access vi the Internet Here the web server performs front end processing for the da tabase server and 
the firewall allows only specific protocol for communication between th external segment and the DMZ as well as 
between the DMZ and the intern al segment Direct communi cation between the external segment and the internal 
segment is not allowed Which of the following can be used to interconnect multiple LANs on the network layer layer 
of the OSI basic reference model and to relay packets of data Which of the following is prot ocol that is used for 
synchr onization of the internal clock of computer via network with se rver that holds reference clock In an IPv4 
network which of the following is the correct combination of an IP address class its IP address range and subnet 
mask class range subnet mask Among the descriptions from through which of the following is the list that contains 
all and only appropriate features of VPN Devices can communicate with each other by using VPN wirelessly without 
passing through any access point VPN uses public network etc but it ca be used like private network of one own 
company The security status of computers can be checked by connecting them to VPN In an IPv4 environment when the 
subnet mask 255 255 255 224 is used for class network how many IP addresse including reserved or inef fective 
addresses can be assigned to subnets and host per subnet respectively Number of IP addresses Subnet Host Which of 
the following is feature of sw itching hub layer sw itch network device Read the following description of compa ny 
network and then answer Subquestions and Company has branch office BO located ab out 20 km from the head office HO 
The branch office has LAN BO LAN of 50 us ers and the head office has LAN HO LAN of 80 users who share devices nd 
information The head office has DNS server and Web server www example com in the server networ to facilitate users 
of both LANs to use information stored in the Web server BO LAN is connected to the router R1 Both HO LAN and the 
server network are connected to th router R2 R1 and R2 are connected each other PCs in BO LAN obtain IP addresses 
au tomatically from the DHCP server PCs in HO LAN are configured statically Figure shows the network connectivity 
and Ta ble shows the information about networks and devices Figure Network connectivity Sw1 DNS Server Web 
ServerDHCP ServerS01 Network Printer172 16 R1 R2172 16 2S02 172 16 10fe02 172 16 10fe01 Sw2Sw3172 16 10fe01 172 16 
24Server Network PC B01 172 16 102DNS 172 16 103Web Server PC B50 PC H01 PC H80172 16 24Network BO LAN 172 16 
24Network HO LAN Network PrinterRouter Network 172 16 30 14 Table Information about networks and devices Network 
name Location Network address Devices Gateway BO LAN Branch office 172 16 24 PC B01 to PC B50 DHCP server network 
printer Fast Ethernet 01 fe01 of R1 HO LAN Head Office 172 16 24 PC H01 to PC H80 network printer Fast Ethernet 01 
fe01 of R2 Server Network Head Office 172 16 24 DNS Server Web Server Fast Ethernet 02 fe02 of R2 R1 to R2 172 16 
30 R1 and R2 Subquestion From the answer groups below select the co rrect answer to be inserted in each blank 
_______ in the following description The IP addresses are sub netted to separate the network laye broadcast domain 
and enable routers to route the messages When new PC in BO LAN requires an IP address and corresponding network 
inf

Which of the following is an appropriate description concerning symptom and its measures to be taken at the 
occurrence of file fragmentation Which of the following is an appropriate description concerning and MTTR Which of 
the following is an appropriate descriptio concerning the virtualization of server Which of the following is an 
appropriate description of rollback in transaction processing Which of the following is an appropr iate description
of blade server Among the IoT application examples which of the following is an explanation of HEMS Which of the 
following is an appropriate explanation of the POP communications protocol Which of the following is an explanation
of contact management that is basic function of SFA Sales Force Automation Which of the following is an explanation
concernin the reliability index that is calculated by the expression below MTBF MTBF MTTR Which of the following is
an appropr iate description of Trojan horse Among advertisements on the Internet which of the following is an 
appropriate explanation of banner advertisement Which of the following is an appropriate explanation of XBRL Which 
of the following is an appropriate explanation of ava ilability concerning RASIS Which of the following is an 
appropriate description of the constituent elements of IoT Which of the following is an appropriate de scription 
concerning th operations of quality management system in accordance with ISO 9001 2008 Which of the following is an
explanation of green procurement Which of the following is an appropriate descripti on concerning file management 
under UNIX Which of the following is an appropriate description concerning Which of the following is an appropriate
descriptio of cloud computing Which of the following is the most appropr iate description con cerning an interview 
conducted by system auditor Which of the following is an appr opriate description concerning of the following is an
appr opriate explanation of an ASP Which of the following is an explanation of free software Which of the following
is an appropriate descripti on concerning cache memory Which of the following is an appropriate description 
concerni hot site pr epared as backup system Which of the following is an explanation of acceptance testing 
performed for new system Which of the following is an appropriate explanation of the regression test Which of the 
following is an explanation of SQL in jection Which of the following is an ppropriate explanation of ASP In 
software development which of the following is an appropriate description concerning test Which of the following is
the explanation of control chart Which of the following is an appropriate descriptio of multi core processor Which 
of the following is an appropriate descriptio concerning flash memory Which of the following is the most 
appropriate description concerning management that is to be planned for the development environment of an embedded 
system used during the development of product Which of the following is an appropriate description of phishing 
Which of the following is an explanation of texture mapping Which of the following is an appropriate descriptio 
concerning the role of system auditor Which of the following is an appropriate explanation of opi nion leaders who 
are thought to be important for market penetration of new product Which of the following is an ppropriate 
explanation of CAD Which of the following is the most appropriate explanation of phishing Which of the following is
an appropriate de scription concerning the characteristics of EUC End User Computing Which of the following is an 
appropriate explanation of MP3 that is used as multimedia file format Which of the following is an appropriate 
explanation of memory mapped Which of the following is an appropriate descripti on concerning the characteristics 
of an interpreter based program Which of the following is an explanation of SaaS Which of the following is an appr 
opriate explanation

After the detailed design of an information system is complete it is decided to outsource programming to an 
outsourcing contractor with clearly defi ned specifications deliverables and scope of work Which of the following 
is th most appropriate management activity of the project manager of the ordering company As shown in the arrow 
diagram below there exists project consisting of nine activities through When the number of days required for 
activity is shortened from days to days by how many days can the minimum number of days required for this project 
be shortened What is the number of days required to complete the development of software project is planned to 
complete in 12 months and the budget for the completion of the project is 100 000 After six months it is found tha 
60 000 are spent but only 40 of the work is completed If the Cost Performance Index CPI is ot changed what is the 
estimated amount in dollars required to complete the remaining tasks of the project Which of the following is the 
name of communication standard that is used in mobile phone networks and has the three ch aracteristics described 
below All communications are processe with packet switching scheme It is possible to use communication scheme 
called MIMO that uses multiple antennas It has been standardized in the international standardization project 3GPP 
3rd Generation Partnership Project The activities and nodes of project are shown in the arro diagram below Which of
the following is the effect of extending the duration of activity by days The table below shows the series of 
activit ies for certain project The numbers in the table indicate the cost of each activity nd how long in weeks it
takes to complete each activity Prior to starting each activity the previous activities shown in the table must be 
completed When the weekly cost of the project is minimized without delay of the project what is the hi ghest weekly
cost in dollars during this project Here the weekly cost remains stable nd unchanged during each activity Activity 
Time in weeks Cost Previous activities 900 400 250 4200 900 350 1800 Completed Project management areas are cl 
assified into project cost management project scope management pr oject quality management pr oject risk management
and other areas Which of the follow ing is an appropriate activity performed in project quality management When the
outsourced development project of system has passed beyond its halfway mark there is request from the outsourcer 
for adding unction to the system Which of the following is the most appropri ate action of the project manager In 
an activity that is performe in the planning phase of pro ject which of the following is method that identifies all
of the activitie that need to be performed in the project and organizes them in hierarchical structure as well as 
clar ifying the management units of the project In development project after software integration test is completed
system test is being conducted to check the functions of system Acco rding to the system test report there are many
defects in certain program Which of the following is the most appropriate action that the pr oject manager should 
take first The table below shows seven activities their rela tionships and the number of days required to complete 
each activity in software de velopment project When the activities and begin simultaneously and are performed in 
parallel which of the following is an appropriate Gantt chart that corres ponds to this table Activity Preceding 
activity Number of days required When system development project is started whic of the following is the 
appropriate stage for setting the target values for quality co st and delivery date Which of the following is an 
appropriate xplanation concerning milestone in project management project management is necessary to manage co st 
time quality and other factors Which of the following is an appropriate descriptio concerning project management 
de

Which of the following is an explanation of the maturity stage in the product life cycle There are Sales Customer 
and Product tables in relational database Among lists through which of the following cont ains all and only the 
lists that can be created from the data in these tables Here solid underlined part represents pr imary key and 
dashed underlined column represents foreign key Sales SalesNumber CustomerNumber ProductNumber SalesDate 
SalesAmount Customer CustomerNumber CustomerName Product ProductNumber ProductCategoryName ProductName The list of 
customers ho bought more than certain amount of money during certain period in the past The list of products that 
were out of stock in the previous month The ranking list for sales amount by product in the previous month In sales
company the number of actually stocked products is 100 at the end of April and the order transactions are recorded 
until May as shown in the table below When products come into stock in days after an order placed how many stocked 
products are available for allocation on May 10 Here holi days of the sales company and its trading partners do not
need to be considered and transactions prior to the previous month can also be ignored Transaction date Orders 
received Orders placed May 40 units May 50 units May 20 units May 50 units May 30 units Product portfolio 
management is method fo analyzing the positioning of product within the market and reviewing the resour ce 
allocation It uses matrix chart divided into four quadrants with the market growth rate on the vertical axis and 
the market share on the horizontal axis Which of the following refers to product that is categorized into the 
quadrant for low mark et growth rate and high market share Which of the following inventory va luation methods 
calculates he inventory unit price by dividing the total purchase amount by the total quantity of items purchased 
at the end of the accounting period Which of the following is applicable to in the comparison table below that 
shows the characteristics of each production system of co ntinuous production individual production lot production 
and process production Production system Production quantity Small Medium Large Large Form of Main production Build
to order Build to order build to stock Build to stock Build to order build to stock Type of product Many Some Few 
Few Frequency of arrangements High Medium Low Very low Processing example Assembly Assembly Assembly Chemical When 
the results of financial statement anal ysis for the current period are as shown in the table below which of the 
following is th cost of sales in thousands of dollars Cost of sales ratio 80 Ratio of operating profit to net sales
10 Operating profit 20 000 dollars factory is engaged in assembly production of product that consists of components
and The processing of component requires component and the processing period is one week The delivery lead times of
purchased components and are two weeks and three weeks respectively Product can be assembled in one week only after
components and are both delivered What is the minimum number of weeks required to produce one unit of product 
including the delivery periods of the components Here there is no stock of any of the components In the case of 
constructing new system by either developi ng new system or adopting an existing package when the in itial 
investment amount effect amount operational cost and maintenan ce cost are as shown in the table below which of the
following is the method for recovering the initial investment amount in the minimum number of years System 
construction method Initial investment amount dollars Effect amount dollars year Operational cost dollars year 
Maintenance cost dollars year The product life cycle is con cept based on the idea that al products pass through 
four stages introduction growth maturity and decline Which of the following is the characteristic of the maturity 
stage in the product life cycl

[('sales table', 0.5732),
 ('product sales', 0.5482),
 ('products table', 0.5185),
 ('concerning sales', 0.5182),
 ('sales analyzed', 0.5094),
 ('product table', 0.508),
 ('product inventory', 0.5076),
 ('determine sales', 0.5062),
 ('sales data', 0.5011),
 ('sales quantity', 0.4994)]

In [ ]:
keywords[0]

('sales table', 0.5732)

# **Save to JSON**

In [ ]:
data = db.collection('exams').stream()
ids = [id.id for id in data]

In [ ]:
len(ids)

exams_data = {}

for id in ids:
  data = db.collection('exams').document(id).get().to_dict()
  exams_data[id] = data

In [ ]:
exams_data['7Vr2arhldDnIE3Nj1hLT']

{'exam_name': '2015S_IP_Question.pdf',
 'answers': ['It is an ultra-small computer in which the CPU, main memory, and interface circuits \nare embedded in a single chip.',
  'It is a large computer that is used for a wide r ange of applications from office \nprocessing to technical calculations, including mis sion-critical business as the main \ntarget.',
  'It is a client-dedicated computer that is equipp ed only with the minimum functions, \nsuch as data entry and display, in the configuratio n of a system where resources, \nsuch as the application programs and files, are man aged at the server side.',
  'It is a portable information terminal where func tions, such as schedule management,'],
 'question_number': 21,
 'question': 'Q21. Which of the following is an appropriate explanatio n of a general purpose computer that is also known as a mainframe?'}

In [ ]:
list_exams_data = [exams_data[id] for id in ids]

In [ ]:
import json

json_obj = json.dumps(list_exams_data, indent=4, ensure_ascii=False)

with open('/content/drive/MyDrive/itpe_exams/itpe_exams.json', 'w', encoding="utf-8") as f:
  f.write(json_obj)